# Proyección de las trayectorias con cMDS

In [41]:
import pandas as pd
import numpy as np
import pytraj as pyt
import glob, os, sys
import pickle
# Añadimos la ruta del directorio raíz para tener acceso a los archivos y módulos
sys.path.append(r'..')

## Carga de los datos de referencia

In [42]:
prot_name = 'cdk2'

In [43]:
# Este es el DF que no tiene aun afgregados los valores AUC de las conformaciones
path_to_json_file = glob.glob((os.path.join('..', 'data', 
                        F'TABLA_MTDATA_{prot_name.upper()}_*_crys_LIGS_INFO_LABELS.json')))[0]
                      
df_prot = pd.read_json(path_to_json_file)

In [44]:
from modules.subsecuencias_cdk2 import *
pisiani_residues = get_pisani_residues(sep=",")
pocket_residues = get_pocket_residues(sep=",")

In [45]:
mask_pisani = F"(:{pisiani_residues})&(@CA)"

In [46]:
# Carga del objeto cMDS de las 402 estructuras cristalográficas
path_mds_obj = os.path.join('..', 'data', 'trajectory_analysis', 'cMDS_Pisani_402_obj.pyobj')
#
with open(path_mds_obj, 'rb') as f:
    mds_pisani_402 = pickle.load(f)

In [47]:
import matplotlib.pyplot as plt
import seaborn as sns
sns.set(context = 'talk', style = 'white')
from modules.plotting_functions import plot_points, plot_anotation_labels

In [48]:
mds_plot = mds_pisani_402

## Proyección de trayectorias
### Cargamos el json con las proyecciones

In [49]:
path_mds_obj = os.path.join('..', 'data', 'trajectory_analysis', 'mds_all_traj_projections.obj')
#
with open(path_mds_obj, 'rb') as f:
    dic_trajs = pickle.load(f)

## Visualización con bokeh

In [50]:
from bokeh.plotting import show, figure
from bokeh.io import output_notebook
from bokeh.models import ResetTool, PanTool, WheelZoomTool, \
ColumnDataSource, Span, HoverTool, LabelSet, Range1d

In [51]:
from matplotlib.colors import LinearSegmentedColormap, rgb2hex
from matplotlib import cm

In [55]:
output_notebook()

Loading BokehJS ...

In [61]:
# tools reference
HOVER = HoverTool(names=["ref"])
TOOLTIPS = [
    ("index", "$index"),
    ("PDB ID", "@pdb_id"),
    ("conf", "@conf_label")]
TOOLS = ['pan', 'wheel_zoom', HOVER, ResetTool()]

f = figure(plot_width = 900, plot_height = 800,
           title = 'Proyección de las trayectorias',
           match_aspect=True, active_scroll='wheel_zoom',
           tooltips = TOOLTIPS, tools = TOOLS)


# Styling del plot
f.title.text_font_size = '2em'

# Axis
f.axis.axis_line_width = 3.3
f.axis.major_label_text_font_size = '1.1em'
f.axis.major_label_text_font_style = 'bold'

# Labels
f.axis.axis_label_text_font_size = '1.4em'
f.xaxis.axis_label = 'Dimensión 1'
f.yaxis.axis_label = 'Dimensión 2'

# Grid

# Plot de la referencia de pisani
ref_pisani = ColumnDataSource({
    'x': mds_plot[0][0], 'y': mds_plot[0][1]})

# Datasource referencia
conformation_labels = df_prot.Labels_conf
conf_labels = conformation_labels.unique()
ref_pisani = ColumnDataSource(data = dict(
    x = mds_plot[0][0],
    y = mds_plot[0][1],
    pdb_id = df_prot.index.to_series().apply(lambda x: x.upper()),
    conf_label = conformation_labels,
))

# Vertical line
vline = Span(location=0, dimension='height', 
             line_color='grey', line_width=2, line_dash='dashed')
# Horizontal line
hline = Span(location=0, dimension='width', 
             line_color='grey', line_width=2, line_dash='dashed')
f.renderers.extend([vline, hline])

# Proyección de referencia
f.scatter('x', 'y', source = ref_pisani, name = 'ref',
          size = 10, alpha = 0.7, color = '#cccccc', 
          line_color = '#888888')

f.toolbar_location = 'above'
f.toolbar.logo = None

# List of key structures
list_of_keys = ['1fin', '4fku', '3pxf', '5a14']
colormaps = ['Spectral', 'Spectral_r', 'BrBG', 'viridis_r']
# Proyección de las diferentes réplicas
interval = 10
palettes = dict(zip(list_of_keys, colormaps))
print(palettes)
for conf, system in dic_trajs['cdk2'].items():
    palette = palettes[conf]
    cmap = cm.get_cmap(palette, len(system)*3)
    colors = [rgb2hex(cmap(i)[:3]) for i in range(cmap.N)]
    for c, method in enumerate(system.keys()):
        if system[method] is not None:
            for i, j in system[method].items():
                system_legend = F'{conf}: {method}'
                f.scatter(x = j[0][::interval], y = j[1][::interval], 
                          color = colors[c],  alpha = 0.9, 
                          muted_color = colors[c], muted_alpha=0.01,
                          name = system_legend, legend_label = system_legend, size = 6, 
                          marker = 'diamond')
                
list_of_keys_positions = [df_prot.index.get_loc(i) for i in list_of_keys]
# plotting labels
df_ref_conf = pd.DataFrame(dict(
            x = mds_plot[0][0][list_of_keys_positions],
            y = mds_plot[0][1][list_of_keys_positions],
            pdb_id = df_prot.index.to_series().apply(lambda x: x.upper())[list_of_keys_positions],
            conf_label = conformation_labels[list_of_keys_positions]
    ))
ref_conformations = ColumnDataSource(data = df_ref_conf)

# Proyección de conformaciones iniciales
f.scatter('x', 'y', source = ref_conformations,
          size = 10, color = '#E3E305', line_width = 3,
          line_color = 'black')
labels = LabelSet(x = 'x', y= 'y', text = 'pdb_id', 
                  source = ref_conformations, 
                  background_fill_color = 'white',
                  background_fill_alpha = 0.8,
                  x_offset=5, y_offset=5,
                  text_font_style = 'bold')
f.add_layout(labels)

# Limits
#f.x_range = Range1d(-2, 2, bounds = (-2.5, 2.5))
#f.y_range = Range1d(-1.5, 1.5, bounds = (-2.5, 2.5))

f.legend.click_policy="mute"
f.legend.location = 'top_left'

#output_notebook()
show(f)

{'1fin': 'Spectral', '4fku': 'Spectral_r', '3pxf': 'BrBG', '5a14': 'viridis_r'}


### Proyección con gráficas de contorno

In [13]:
from modules.plotting_functions import density_estimation
import plotly.graph_objs as go
import plotly
plotly.offline.init_notebook_mode()

In [14]:
fig = go.Figure()

fig.add_trace( go.Scatter(
            x = mds_plot[0][0], y = mds_plot[0][1],
            xaxis = 'x', yaxis = 'y', text = df_prot.index.to_list(),
            mode = 'markers', showlegend= False,
            marker = dict(
                color = 'rgba(142,156,159,0.2)',
                size = 10 )
    ))

palettes = {'1fin': 'Spectral', '4fku': 'Spectral_r'}
for conf, system in dic_trajs['cdk2'].items():
    palette = palettes[conf]
    cmap = cm.get_cmap(palette, len(system)*3)
    colors = [rgb2hex(cmap(i)[:3]) for i in range(cmap.N)]
    for c, method in enumerate(system.keys()):
        if system[method] is not None:
            x_ = []; y_ = []
            a = system[method]
            for i, key in enumerate(a.keys()):
                x_ = x_ + list(a[key][0]); y_ = y_ + list(a[key][1])
            x_ = np.array(x_); y_ = np.array(y_)
            fig.add_trace(
                go.Histogram2dContour(
                    x = x_, y = y_,
                    colorscale = [[0, colors[c]], [1, colors[c]]],
                autocontour = False,
                ncontours = 25, histnorm = 'density',
                showscale = False, line = {'width': 1},
                contours = {'type': 'levels',  'coloring': 'lines'},
                showlegend=True, hoverinfo='skip',
                name = F'{conf.upper()}: {method}'))
            
fig.add_trace(go.Scatter(
    x = mds_plot[0][0][[idx_4fku, idx_1fin]],
    y = mds_plot[0][1][[idx_4fku, idx_1fin]],
    mode = 'markers+text', showlegend= False,
    text = ['4FKU', '1FIN'], textposition="top center", 
    textfont = dict(color='white'), marker = dict(size = 10)))


fig.update_layout(
    title="cMDS: Proyección de las Trayectorias",
    xaxis_title="Dimensión 1",
    yaxis_title="Dimensión 2",
    width = 950, height = 950,
    yaxis = dict(scaleanchor = "x", scaleratio = 1),
    plot_bgcolor = '#1a1a1a', dragmode = 'pan',
    font = dict(size = 15),
    legend = go.layout.Legend(
        x=0, y=1, traceorder="normal",
        font = dict(
            family="sans-serif",
            size=13,
            color="white"
        ),
        bgcolor="rgba(20,20,20,0.4)",
    )
)

fig.update_xaxes(zeroline=True, zerolinewidth=3, zerolinecolor = '#333',
                 showgrid=True, gridwidth=1, gridcolor='#222',
                 showline=True, linewidth=3, linecolor='black')
fig.update_yaxes(zeroline=True, zerolinewidth=3, zerolinecolor = '#333',
                 showgrid=True, gridwidth=1, gridcolor='#222',
                 showline=True, linewidth=3, linecolor='black')

fig.show()